Lambda School Data Science, Unit 2: Predictive Modeling

# Regression & Classification, Module 2

## Assignment

You'll continue to **predict how much it costs to rent an apartment in NYC,** using the dataset from renthop.com.

- [ ] Do train/test split. Use data from April & May 2016 to train. Use data from June 2016 to test.
- [ ] Engineer at least two new features. (See below for explanation & ideas.)
- [ ] Fit a linear regression model with at least two features.
- [ ] Get the model's coefficients and intercept.
- [ ] Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.
- [ ] What's the best test MAE you can get? Share your score and features used with your cohort on Slack!
- [ ] As always, commit your notebook to your fork of the GitHub repo.


#### [Feature Engineering](https://en.wikipedia.org/wiki/Feature_engineering)

> "Some machine learning projects succeed and some fail. What makes the difference? Easily the most important factor is the features used." — Pedro Domingos, ["A Few Useful Things to Know about Machine Learning"](https://homes.cs.washington.edu/~pedrod/papers/cacm12.pdf)

> "Coming up with features is difficult, time-consuming, requires expert knowledge. 'Applied machine learning' is basically feature engineering." — Andrew Ng, [Machine Learning and AI via Brain simulations](https://forum.stanford.edu/events/2011/2011slides/plenary/2011plenaryNg.pdf) 

> Feature engineering is the process of using domain knowledge of the data to create features that make machine learning algorithms work. 

#### Feature Ideas
- Does the apartment have a description?
- How long is the description?
- How many total perks does each apartment have?
- Are cats _or_ dogs allowed?
- Are cats _and_ dogs allowed?
- Total number of rooms (beds + baths)
- Ratio of beds to baths
- What's the neighborhood, based on address or latitude & longitude?

## Stretch Goals
- [ ] If you want more math, skim [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf),  Chapter 3.1, Simple Linear Regression, & Chapter 3.2, Multiple Linear Regression
- [ ] If you want more introduction, watch [Brandon Foltz, Statistics 101: Simple Linear Regression](https://www.youtube.com/watch?v=ZkjP5RJLQF4)
(20 minutes, over 1 million views)
- [ ] Add your own stretch goal(s) !

In [ ]:
import os, sys
in_colab = 'google.colab' in sys.modules

# If you're in Colab...
if in_colab:
    # Pull files from Github repo
    os.chdir('/content')
    !git init .
    !git remote add origin https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification.git
    !git pull origin master
    
    # Install required python packages
    !pip install -r requirements.txt
    
    # Change into directory for module
    os.chdir('module2')

In [ ]:
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [1]:
import numpy as np
import pandas as pd

# Read New York City apartment rental listing data
df = pd.read_csv('../data/apartments/renthop-nyc.csv')
assert df.shape == (49352, 34)

# Remove the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= np.percentile(df['price'], 0.5)) & 
        (df['price'] <= np.percentile(df['price'], 99.5)) & 
        (df['latitude'] >= np.percentile(df['latitude'], 0.05)) & 
        (df['latitude'] < np.percentile(df['latitude'], 99.95)) &
        (df['longitude'] >= np.percentile(df['longitude'], 0.05)) & 
        (df['longitude'] <= np.percentile(df['longitude'], 99.95))]

In [20]:
df.head(50)

bathrooms  bedrooms             created  \
0         1.5         3 2016-06-24 07:54:24   
1         1.0         2 2016-06-12 12:19:27   
2         1.0         1 2016-04-17 03:26:41   
3         1.0         1 2016-04-18 02:22:02   
4         1.0         4 2016-04-28 01:32:41   
5         2.0         4 2016-04-19 04:24:47   
6         1.0         2 2016-04-27 03:19:56   
7         2.0         1 2016-04-13 06:01:42   
8         1.0         1 2016-04-20 02:36:35   
9         2.0         4 2016-04-02 02:58:15   
10        1.0         0 2016-04-14 01:10:30   
11        1.0         1 2016-06-03 03:21:22   
12        1.0         2 2016-04-19 05:37:25   
13        2.0         2 2016-04-09 01:22:11   
14        1.0         1 2016-06-01 03:11:01   
15        1.0         0 2016-04-18 02:36:00   
16        1.0         2 2016-04-22 05:57:16   
17        1.0         1 2016-04-19 03:36:28   
18        1.0         4 2016-04-20 04:00:32   
19        1.0         1 2016-04-09 03:49:42   
20        1.0         3 2016-04-12 02:39:45   
21        1.0         2 2016-04-07 02:11:45   
22        1.0         1 2016-04-13 05:17:43   
23        1.0         1 2016-04-17 02:26:52   
24        2.0         4 2016-06-07 04:39:56   
25        3.5         4 2016-04-27 06:43:40   
26        1.0         1 2016-04-25 02:29:50   
27        1.0         1 2016-04-22 05:39:10   
29        2.0         2 2016-04-26 02:59:37   
30        1.0         0 2016-04-21 02:17:28   
31        1.0         2 2016-04-04 04:10:01   
32        1.0         1 2016-04-22 04:58:35   
33        1.0         2 2016-04-20 02:43:19   
34        1.0         2 2016-06-17 03:30:24   
35        1.0         1 2016-04-18 03:34:14   
37        1.0         0 2016-04-17 02:16:42   
38        2.0         2 2016-04-06 06:27:51   
39        1.0         0 2016-06-29 04:08:35   
40        1.0         3 2016-04-18 04:46:30   
41        3.0         4 2016-04-12 05:21:21   
42        1.0         0 2016-04-19 06:19:44   
43        1.0         0 2016-04-29 05:27:33   
44        1.0         1 2016-04-09 01:13:37   
45        1.0         1 2016-04-25 21:03:08   
46        1.0         0 2016-04-29 04:31:19   
47        1.0         2 2016-04-09 02:19:04   
48        1.0         1 2016-06-21 04:09:32   
49        1.0         2 2016-04-11 15:59:59   
50        1.0         1 2016-04-21 06:33:48   
51        1.0         1 2016-04-30 01:22:06   

                                          description  \
0   A Brand New 3 Bedroom 1.5 bath ApartmentEnjoy ...   
1                                                       
2   Top Top West Village location, beautiful Pre-w...   
3   Building Amenities - Garage - Garden - fitness...   
4   Beautifully renovated 3 bedroom flex 4 bedroom...   
5                                                       
6   Stunning unit with a great location and lots o...   
7   This huge sunny ,plenty of lights 1 bed/2 bath...   
8                            <p><a  website_redacted    
9   This is a spacious four bedroom with every bed...   
10  New to the market! Spacious studio located in ...   
11  Check out this one bedroom apartment in a grea...   
12  ***LOW FEE. Beautiful CHERRY OAK WOODEN FLOORS...   
13  Lincoln Square's premier full service building...   
14  Spacious 1-Bedroom to fit King-sized bed comfo...   
15  Stunning  full renovated studio unit. High cei...   
16  East Village is a great community with great p...   
17  *Location: Thayer St. &amp; Broadway, Manhatta...   
18                                                      
19                                                      
20  BEAUTIFUL 2 BEDROOM POSSIBLE CONVERSION INTO T...   
21  No fee huge two bedroom apartment. Great locat...   
22                                                      
23  CooperCooper.com :: Web ID #179546; Access 100...   
24  SPRAWLING 2 BEDROOM FOUND! ENJOY THE LUXURY OF...   
25  Amazing 4 bedroom convertible. Remarkably luxu...   
26  Don't miss out on this fantastic apartment.......   
27  The TR

In [27]:
from datetime import datetime
df['created'] = pd.to_datetime(df['created'])
train = df[df['created']<= '2016-05-31']
test = df[df['created']> '2016-05-31']

In [28]:
train.head()

bathrooms  bedrooms             created  \
2        1.0         1 2016-04-17 03:26:41   
3        1.0         1 2016-04-18 02:22:02   
4        1.0         4 2016-04-28 01:32:41   
5        2.0         4 2016-04-19 04:24:47   
6        1.0         2 2016-04-27 03:19:56   

                                         description    display_address  \
2  Top Top West Village location, beautiful Pre-w...        W 13 Street   
3  Building Amenities - Garage - Garden - fitness...   East 49th Street   
4  Beautifully renovated 3 bedroom flex 4 bedroom...  West 143rd Street   
5                                                      West 18th Street   
6  Stunning unit with a great location and lots o...  West 107th Street   

   latitude  longitude  price         street_address interest_level  ...  \
2   40.7388   -74.0018   2850        241 W 13 Street           high  ...   
3   40.7539   -73.9677   3275   333 East 49th Street            low  ...   
4   40.8241   -73.9493   3350  500 West 143rd Street            low  ...   
5   40.7429   -74.0028   7995   350 West 18th Street         medium  ...   
6   40.8012   -73.9660   3600  210 West 107th Street            low  ...   

   high_speed_internet  balcony  swimming_pool  new_construction  terrace  \
2                    0        0              0                 0        0   
3                    0        0              0                 0        0   
4                    0        0              0                 0        0   
5                    0        0              0                 0        0   
6                    0        0              0                 0        0   

   exclusive  loft  garden_patio  wheelchair_access  common_outdoor_space  
2          0     0             0                  0                     0  
3          0     0             0                  0                     0  
4          0     0             0                  0                     0  
5          0     0             0                  0                     0  
6          0     0             0                  0                     0  

[5 rows x 34 columns]

In [29]:
test.head()

bathrooms  bedrooms             created  \
0         1.5         3 2016-06-24 07:54:24   
1         1.0         2 2016-06-12 12:19:27   
11        1.0         1 2016-06-03 03:21:22   
14        1.0         1 2016-06-01 03:11:01   
24        2.0         4 2016-06-07 04:39:56   

                                          description      display_address  \
0   A Brand New 3 Bedroom 1.5 bath ApartmentEnjoy ...  Metropolitan Avenue   
1                                                          Columbus Avenue   
11  Check out this one bedroom apartment in a grea...      W. 173rd Street   
14  Spacious 1-Bedroom to fit King-sized bed comfo...       East 56th St..   
24  SPRAWLING 2 BEDROOM FOUND! ENJOY THE LUXURY OF...             W 18 St.   

    latitude  longitude  price           street_address interest_level  ...  \
0    40.7145   -73.9425   3000  792 Metropolitan Avenue         medium  ...   
1    40.7947   -73.9667   5465      808 Columbus Avenue            low  ...   
11   40.8448   -73.9396   1675      644 W. 173rd Street            low  ...   
14   40.7584   -73.9648   3050       315 East 56th St..            low  ...   
24   40.7391   -73.9936   7400              30 W 18 St.         medium  ...   

    high_speed_internet  balcony  swimming_pool  new_construction  terrace  \
0                     0        0              0                 0        0   
1                     0        0              0                 0        0   
11                    0        0              0                 0        0   
14                    0        0              0                 0        0   
24                    1        1              0                 0        1   

    exclusive  loft  garden_patio  wheelchair_access  common_outdoor_space  
0           0     0             0                  0                     0  
1           0     0             0                  0                     0  
11          0     0             0                  0                     0  
14          0     0             0                  0                     0  
24          0     0             0                  0                     0  

[5 rows x 34 columns]

In [37]:
import plotly.express as px
test_trim = test[['bedrooms', 'bathrooms', 'interest_level', 'price']]
train_trim =  train[['bedrooms', 'bathrooms', 'interest_level', 'price']]

In [78]:
train_trim['bed_bath_sum'] = train_trim['bedrooms']+train_trim['bathrooms']
train_trim['bed_bath_ratio'] = train_trim['bedrooms']/train_trim['bathrooms']
key_interest_level = {'low': 1,'medium': 1.25, 'high':1.5}
train_trim.interest_level = [key_interest_level[item] for item in train.interest_level] 
train_trim['total_features'] = df.iloc[:, 10:].sum(axis=1)
train_trim['final_total'] = (train_trim['bed_bath_sum']+train_trim['total_features'])*train_trim['interest_level']
train_trim.head()

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\generic.py:5096: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#

bedrooms  bathrooms  interest_level  price  bed_bath_sum  bed_bath_ration  \
2         1        1.0            1.50   2850           2.0              1.0   
3         1        1.0            1.00   3275           2.0              1.0   
4         4        1.0            1.00   3350           5.0              4.0   
5         4        2.0            1.25   7995           6.0              2.0   
6         2        1.0            1.00   3600           3.0              2.0   

   bed_bath_ratio  total_features  final_total  
2             1.0               3          7.5  
3             1.0               2          4.0  
4             4.0               1          6.0  
5             2.0               0          7.5  
6             2.0               3          6.0

In [75]:
px.scatter(train_trim, x='bed_bath_sum', y='price', trendline='ols')

C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:2389: FutureWarning:

Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.



In [76]:
px.scatter(train_trim, x='bed_bath_ratio', y='price')

In [79]:
test_trim['bed_bath_sum'] = test_trim['bedrooms']+test_trim['bathrooms']
test_trim['bed_bath_ratio'] = test_trim['bedrooms']/test_trim['bathrooms']
key_interest_level = {'low': 1,'medium': 1.25, 'high':1.5}
test_trim.interest_level = [key_interest_level[item] for item in test.interest_level] 
test_trim['total_features'] = df.iloc[:, 10:].sum(axis=1)
test_trim['final_total'] = (test_trim['bed_bath_sum']+test_trim['total_features'])*test_trim['interest_level']
test_trim.head()

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#inde

bedrooms  bathrooms  interest_level  price  bed_bath_sum  bed_bath_ratio  \
0          3        1.5            1.25   3000           4.5             2.0   
1          2        1.0            1.00   5465           3.0             2.0   
11         1        1.0            1.00   1675           2.0             1.0   
14         1        1.0            1.00   3050           2.0             1.0   
24         4        2.0            1.25   7400           6.0             2.0   

    total_features  final_total  
0                0        5.625  
1                5        8.000  
11               0        2.000  
14               3        5.000  
24              11       21.250

In [77]:
px.scatter(test_trim, x='bed_bath_sum', y='price', trendline='ols')

C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:2389: FutureWarning:

Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.



In [64]:
px.scatter(test_trim, x='bed_bath_ratio', y='price')

In [65]:
from sklearn.linear_model import LinearRegression

In [66]:
def linear_regression_rent(features,target,predict = False,bed_bath_sum = None,total_features=None,interest_level=None):
    """I go in depth into what this function does in some of the markdowns I add below.
    However it is not fully functional since I have not made more 'if' parameters to handle all scenarios."""
    
    model = LinearRegression()
    
    x_train = features
    y_train = target
    
    if predict == True:
        if interest_level != None:
            model.fit(x_train, y_train)
            x_test=(bed_bath_sum+total_features)*interest_level
            return model.predict([[x_test]])
        model.fit(x_train, y_train)
        x_test=bed_bath_sum
        return model.predict([[x_test]])
    
    return model.fit(x_train, y_train)